In [6]:
################################
# Scientific imports
################################
import matplotlib.pyplot as plt
import numpy as np

from sktime.datatypes._panel._convert import (
    from_2d_array_to_nested,
    from_nested_to_2d_array,
    is_nested_dataframe,
)

#from sktime.classification.compose import ColumnEnsembleClassifier                 <---- MULTIVARIATE SO NOT NEEDED
#from sktime.classification.dictionary_based import BOSSEnsemble                    <---- MULTIVARIATE SO NOT NEEDED
from sktime.classification.dictionary_based import IndividualBOSS
from sktime.classification.dictionary_based import ContractableBOSS
from sktime.classification.dictionary_based import MUSE
from sktime.classification.dictionary_based import IndividualTDE
from sktime.classification.dictionary_based import TemporalDictionaryEnsemble
from sktime.classification.dictionary_based import WEASEL
from sktime.classification.distance_based import ElasticEnsemble
from sktime.classification.distance_based import ProximityForest
from sktime.classification.distance_based import ProximityStump
from sktime.classification.distance_based import ProximityTree
from sktime.classification.distance_based import ShapeDTW
from sktime.classification.distance_based import KNeighborsTimeSeriesClassifier
#from sktime.classification.feature_based import Catch22Classifier                  <---- MULTIVARIATE SO NOT NEEDED
from sktime.classification.feature_based import MatrixProfileClassifier
from sktime.classification.feature_based import SignatureClassifier
from sktime.classification.feature_based import TSFreshClassifier
#from sktime.classification.hybrid import Catch22ForestClassifier                   <---- For some reason this one doesn't work? Or, rather, gives me an error
from sktime.classification.hybrid import HIVECOTEV1
from sktime.classification.hybrid import HIVECOTEV2
from sktime.classification.interval_based import CanonicalIntervalForest
from sktime.classification.interval_based import DrCIF
from sktime.classification.interval_based import RandomIntervalSpectralForest
from sktime.classification.interval_based import SupervisedTimeSeriesForest
#from sktime.classification.interval_based import TimeSeriesForestClassifier        <---- MULTIVARIATE SO NOT NEEDED
from sktime.classification.kernel_based import Arsenal
from sktime.classification.kernel_based import ROCKETClassifier
from sktime.classification.shapelet_based import ShapeletTransformClassifier
#from sktime.classification.shapelet_based import MrSEQLClassifier                  <---- MULTIVARIATE SO NOT NEEDED

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score

################################
# General imports
################################
import csv, math, io, os, os.path, sys, random, time, json, gc
import pandas as pd
import argparse
from datetime import datetime

In [7]:
################################
# Suppress Warnings
################################
import warnings
warnings.simplefilter(action='ignore', category=UserWarning)
warnings.simplefilter(action="ignore", category=RuntimeWarning)

In [8]:
################################
# Initialisers
################################

# Load the Data files
#fitsarr = np.load("fitslist.npy")

################################
# Functions
################################

def WriteJSON(targetname, acc, pre, rec):
    # Preparing the stats text
    data = {}
    data[targetname] = []
    data[targetname].append({
        'Accuracy' : acc,
        'Precision' : pre,
        'Recall' : rec
    })

    # File saving stuff
    targetdest="./confusionmatrices/sktime_"
    fname = targetname+".json"

    print("Saving {}".format(fname))

    # Write all the info to a file
    with open(targetdest+fname, "w") as f:
        #f.write(stats)
        json.dump(data, f, indent=4, default=str)
    

In [4]:
print("Loading X and Y...")
X = np.array([item[1:-1] for item in np.load("None_Or_One_Exoplanet_NORMALISED.npy")])
y = np.load("one_or_none_isplanetlist.npy")


Loading X and Y...


In [5]:
print("Splitting into Test and Train sets...")
X_nested = from_2d_array_to_nested(X)

Splitting into Test and Train sets...


In [6]:
X_train, X_test, y_train, y_test = train_test_split(X_nested, y)

In [36]:
    # List of all classifiers
    #
#
# SOME OF THESE MIGHT NOT BE NEEDED!
# See: (https://www.sktime.org/en/stable/examples/03_classification_multivariate.html) for MULTIVARIATE ones - I have UNIVARIATE
#
print("Load Classifier list...")
list_of_classifiers = [
#ColumnEnsembleClassifier(estimators=20),   # < this is the only one where I believe you *need* a param; the others seem fine without it
#BOSSEnsemble(),
        IndividualBOSS,
        ContractableBOSS,
MUSE,
        IndividualTDE,
        TemporalDictionaryEnsemble,
        WEASEL,
        ElasticEnsemble,
        ProximityForest,
        ProximityStump,
        ProximityTree,
        ShapeDTW,
        KNeighborsTimeSeriesClassifier,
#Catch22Classifier(),
        MatrixProfileClassifier,
        SignatureClassifier,
        TSFreshClassifier,
#Catch22ForestClassifier(),
        HIVECOTEV1,
        HIVECOTEV2,
        CanonicalIntervalForest,
        DrCIF,
       RandomIntervalSpectralForest,
        SupervisedTimeSeriesForest,
#TimeSeriesForestClassifier(),
        Arsenal,
        ROCKETClassifier,
        ShapeletTransformClassifier,
#MrSEQLClassifier()
]

Load Classifier list...


In [8]:
from dask.distributed import Client

client = Client()
client

Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.


<Client: 'tcp://127.0.0.1:46399' processes=4 threads=8, memory=59.14 GiB>

In [22]:
import dask.bag

In [23]:
bag = dask.bag.from_sequence(list_of_classifiers)

In [24]:
X_train.iloc[:10]

0
8978  0        1.000763
1        0.999926
2        0...
2851  0        1.000124
1        1.000644
2        1...
7213  0        1.002660
1        1.004248
2        1...
6534  0        0.997019
1        0.994858
2        0...
6572  0        0.999625
1        0.999892
2        1...
2078  0        0.935551
1        0.931637
2        0...
1477  0        1.000922
1        1.002699
2        1...
714   0        0.993197
1        0.990749
2        0...
3834  0        0.985587
1        0.984358
2        0...
8898  0        1.001609
1        0.999108
2        0...

In [14]:
    print("Loading X and Y...")
    X = np.array([item[1:-1] for item in np.load("None_Or_One_Exoplanet_NORMALISED.npy")])
    y = np.load("one_or_none_isplanetlist.npy")

Loading X and Y...


In [15]:
len(X)

9154

In [41]:
def myfunc(classifierType, rows):
    X = np.array([item[1:-1] for item in np.load("None_Or_One_Exoplanet_NORMALISED.npy")])
    y = np.load("one_or_none_isplanetlist.npy")
    
    X = X[:rows, :]
    y = y[:rows]
    
    print("Splitting into Test and Train sets...")
    X_nested = from_2d_array_to_nested(X)
    
    X_train, X_test, y_train, y_test = train_test_split(X_nested, y)
    
    c = classifierType()
    
    c.fit(X_train, y_train)
    
    dump(c, f'{classifierType.__name__}_fitted_{rows}.joblib')

In [40]:
list_of_classifiers[0].__name__

'IndividualBOSS'

In [ ]:
list_of_classifiers

In [34]:
from joblib import Parallel, delayed

In [42]:
Parallel(n_jobs=4)(delayed(myfunc)(c, 10) for c in list_of_classifiers)

/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-pac

Splitting into Test and Train sets...
Splitting into Test and Train sets...


/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning:

Splitting into Test and Train sets...
Splitting into Test and Train sets...


Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning: invalid value encountered in true_divide
  msb = ssbn / float(dfbn)
/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/feature_selection/_univariate_selection.py:108: RuntimeWarning:

ValueError: Found array with 0 feature(s) (shape=(7, 0)) while a minimum of 1 is required.

In [17]:
c = IndividualBOSS()

In [11]:
c.fit(X_train, y_train) ## 200 records

IndividualBOSS()

In [18]:
c.fit(X_train, y_train)

IndividualBOSS()

In [12]:
from joblib import dump, load

In [19]:
dump(c, 'IndividualBoss_fitted_400.joblib')

['IndividualBoss_fitted_400.joblib']

In [3]:
c = load('IndividualBoss_fitted.joblib')

In [5]:
c.is_fitted

True

In [28]:
def myfunc(classifierType):
    print("Loading X and Y...")
    X = np.array([item[1:-1] for item in np.load("None_Or_One_Exoplanet_NORMALISED.npy")])
    y = np.load("one_or_none_isplanetlist.npy")

    X = X[:20, :]
    y = y[:20]
    
    print("Splitting into Test and Train sets...")
    X_nested = from_2d_array_to_nested(X)
    
    X_train, X_test, y_train, y_test = train_test_split(X_nested, y)
    
    tStart = datetime.now()
    
    classifier = classifierType()
    
    classifier.fit(X_train, y_train)
    cname = type(classifier).__name__
    
  
    y_pred = classifier.predict(X_test)
   
    # Calculate Metrics
    mAcc = accuracy_score(y_test, y_pred)
    mPre = precision_score(y_test, y_pred)
    mRec = recall_score(y_test, y_pred)

    # SAVE TO JSON INSTEAD OF PRINT
    #print(f" > Accuracy: {mAcc}\n > Precision: {mPre}\n > Recall: {mRec}")
    WriteJSON(cname, mAcc, mPre, mRec)

    tFin = datetime.now()
    tDelta = tFin - tStart
    mins = (math.floor(tDelta.seconds/60))
    #print(f"Process took {mins} minutes and {tDelta.seconds - (60*mins)} seconds")


In [29]:
myfunc(list_of_classifiers[0])

Loading X and Y...
Splitting into Test and Train sets...
Saving IndividualBOSS.json


In [30]:
f = client.compute(bag.map(myfunc))

distributed.worker - WARNING - Compute Failed
Function:  execute_task
args:      ((<function reify at 0x7f2fedb70790>, (<function map_chunk at 0x7f2fedb70b80>, <function myfunc at 0x7f2fec63fd30>, [[<class 'sktime.classification.feature_based._tsfresh_classifier.TSFreshClassifier'>]], None, {})))
kwargs:    {}
Exception: AssertionError('daemonic processes are not allowed to have children')

/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/model_selection/_validation.py:771: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/model_selection/_validation.py", line 762, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/srv/conda/envs/saturn/lib/python3.9/site-packages/sklearn/metrics/_scorer.py", line 216, in __call__
    return self._score(
  File "/srv/conda/envs/saturn/lib/python3.9/site-packag

In [26]:
print("Staring Loops!\n####################\n")



classifier = MUSE()
cname = type(MUSE()).__name__

# Tell me what classifier is running currently
print(f"Classifier: {cname}")

Staring Loops!
####################

Classifier: MUSE


In [59]:
classifier.fit(X_train, y_train)

KeyboardInterrupt: 

distributed.client - ERROR - Failed to reconnect to scheduler after 30.00 seconds, closing client
_GatheringFuture exception was never retrieved
future: <_GatheringFuture finished exception=CancelledError()>
asyncio.exceptions.CancelledError


In [5]:
y_pred = classifier.predict(X_test)

# Calculate Metrics
mAcc = accuracy_score(y_test, y_pred)
mPre = precision_score(y_test, y_pred)
mRec = recall_score(y_test, y_pred)

# SAVE TO JSON INSTEAD OF PRINT
print(f" > Accuracy: {mAcc}\n > Precision: {mPre}\n > Recall: {mRec}")
WriteJSON(cname, mAcc, mPre, mRec)

tFin = datetime.now()
tDelta = tFin - tStart
mins = (math.floor(tDelta.seconds/60))
print(f"Process took {mins} minutes and {tDelta.seconds - (60*mins)} seconds")

# Garbage Collection to save memory
del classifier, y_pred, mAcc, mPre, mRec
gc.collect()
print("Garbage Collected!\n")

In [6]:
################################
# EXECUTE ORDER 66
################################

if __name__ == "__main__":
    main()

Loading X and Y...
Splitting into Test and Train sets...
Load Classifier list...
Staring Loops!
####################

Classifier: MUSE


KeyboardInterrupt: 